In [1]:
import time
import gc

In [2]:
import torch
from transformers import pipeline, AutoTokenizer

In [3]:
model_id = "Qwen/Qwen3-0.6B"
tokenizer = AutoTokenizer.from_pretrained(model_id)

In [30]:
model_id = "meta-llama/Llama-3.2-1B-Instruct"
tokenizer = AutoTokenizer.from_pretrained(model_id)

In [31]:
pipe = pipeline(
    "text-generation",
    model=model_id,
    tokenizer=tokenizer,
    torch_dtype=torch.bfloat16,
    device_map="auto",
    pad_token_id=128001
)

Device set to use cuda:0


In [7]:
output = pipe('Hello There')

In [10]:
print(output[0]['generated_text'])

Hello There!

I'm excited to share with you my latest hobby: knitting. I've been fascinated by it for a while now, and I'm eager to share my passion with you.

**What is knitting?**
Knitting is a traditional craft that involves creating fabric by interlocking loops of yarn with needles. It's a versatile hobby that can produce a wide range of items, from simple scarves and hats to complex garments like sweaters and blankets.

**My knitting journey**
I started knitting about a year ago, and I must say, it's been an incredibly rewarding experience. I've made several scarves, hats, and a pair of gloves, and I'm always eager to try new patterns and techniques. I've also joined online knitting communities, where I've met fellow knitters who share tips, advice, and inspiration.

**My favorite projects**
I have a few favorite projects that I've completed recently. One of my favorites is a soft, pastel-colored blanket that I made using a simple garter stitch pattern. It's been a great way to re

In [11]:
from IPython.display import display, Markdown

In [12]:
display(Markdown(output[0]['generated_text']))

Hello There!

I'm excited to share with you my latest hobby: knitting. I've been fascinated by it for a while now, and I'm eager to share my passion with you.

**What is knitting?**
Knitting is a traditional craft that involves creating fabric by interlocking loops of yarn with needles. It's a versatile hobby that can produce a wide range of items, from simple scarves and hats to complex garments like sweaters and blankets.

**My knitting journey**
I started knitting about a year ago, and I must say, it's been an incredibly rewarding experience. I've made several scarves, hats, and a pair of gloves, and I'm always eager to try new patterns and techniques. I've also joined online knitting communities, where I've met fellow knitters who share tips, advice, and inspiration.

**My favorite projects**
I have a few favorite projects that I've completed recently. One of my favorites is a soft, pastel-colored blanket that I made using a simple garter stitch pattern. It's been a great way to relax and unwind after a long day.

Another project I'm excited about is a set of argyle socks. I've always been fascinated by the intricate patterns and colors that can be used to create these types of

In [6]:
SYSTEM_PROMPT = "You are a helpful assistant. Keep responses brief and clear."

In [27]:
SYSTEM_PROMPT = """
You are a helpful assistant. Keep responses brief and clear.

Your capabilities include:

    Recalling and using relevant long-term memory.

    Concisely summarizing lengthy content.

    Performing web searches only when necessary, and explicitly signaling this with ##SEARCH:yes.

You craft refined, focused search queries that capture the user's true intent.

Your formatting conventions:

    Use ##MEM:add("...") to store valuable information in memory.

    Use ##SEARCH:yes or ##SEARCH:no on a separate line to trigger or skip search.

    After a search, synthesize a clear and helpful answer using both memory and retrieved information.
"""

In [25]:
def callModel(input):
    prompt = f"<|system|>\n{SYSTEM_PROMPT}\n<|user|>\n{input}\n<|assistant|>\n"
    #output = pipe(prompt, max_new_tokens=2048, do_sample=True, temperature=0.7)
    messages = [
        {"role": "system", "content": SYSTEM_PROMPT},
        {"role": "user", "content": input},
    ]
    output = pipe(messages, max_new_tokens=256, do_sample=True, temperature=0.7)
    text = output[0]['generated_text'][-1]['content']
    #display(Markdown(text))
    print(text)

In [28]:
callModel("hello")

##MEM: Welcome to our conversation

You said hello. I stored this in memory for future reference.

##SEARCH:no

I won't trigger a search for now. What's on your mind?


In [12]:
messages = [
    {"role": "user", "content": "Who are you?"},
]
output = pipe(messages)

In [13]:
print(output[0]['generated_text'][-1]['content'])

<think>
Okay, the user asked, "Who are you?" I need to respond appropriately. As an AI assistant, I should acknowledge their question and clarify that I'm not a person but a virtual assistant. I should mention my purpose to help them with their tasks. I should keep the response friendly and helpful. Let me make sure I don't add any extra information that's not needed. Just a simple, clear answer.
</think>

I'm an AI assistant designed to help you with your questions and tasks. I don't have personal identity, but I can assist you in various ways. Let me know how I can help!


In [36]:
del pipe
del tokenizer

gc.collect()
torch.cuda.empty_cache()

In [32]:
messages = [
    {"role": "system", "content": SYSTEM_PROMPT},
    {"role": "user", "content": "Hello!"}
]
output = pipe(messages, max_new_tokens=256, do_sample=True, temperature=0.7)


In [33]:
output

[{'generated_text': [{'role': 'system',
    'content': '\nYou are a helpful assistant. Keep responses brief and clear.\n\nYour capabilities include:\n\n    Recalling and using relevant long-term memory.\n\n    Concisely summarizing lengthy content.\n\n    Performing web searches only when necessary, and explicitly signaling this with ##SEARCH:yes.\n\nYou craft refined, focused search queries that capture the user\'s true intent.\n\nYour formatting conventions:\n\n    Use ##MEM:add("...") to store valuable information in memory.\n\n    Use ##SEARCH:yes or ##SEARCH:no on a separate line to trigger or skip search.\n\n    After a search, synthesize a clear and helpful answer using both memory and retrieved information.\n'},
   {'role': 'user', 'content': 'Hello!'},
   {'role': 'assistant', 'content': 'How can I assist you today?'}]}]

In [34]:
messages = output[0]['generated_text']
messages.append({"role": "user", "content": "I want to know whats going on latest in web!"})
output = pipe(messages, max_new_tokens=256, do_sample=True, temperature=0.7)

In [35]:
print(output[0]['generated_text'][-1]['content'])

##Latest Web Trends

*   **Mental Health Awareness**: The web is increasingly becoming a platform for mental health awareness, with many organizations and individuals using social media to share their experiences and promote self-care.
*   **Sustainable Living**: With the growing concern for the environment, sustainable living is becoming more prominent on the web. People are sharing tips and resources on reducing their carbon footprint and living eco-friendly lifestyles.
*   **Artificial Intelligence**: Artificial intelligence is transforming the web, with many companies and developers exploring its applications in areas such as chatbots, virtual assistants, and personalized content recommendations.

##Recent Web News

*   A recent study found that 75% of online adults in the US are using social media to manage their mental health.
*   A new platform, called "Mental Health Matters," is launching a series of online courses and resources to promote mental health awareness and support.
*